In [1]:
import pandas as pd
import numpy as np
from sklearn.neighbors import NearestNeighbors
from scipy.spatial.distance import euclidean

In [2]:
df = pd.read_csv("onehr.csv")

In [3]:
df

date  WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  ...  \
0       1/1/1998   0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9  ...   
1       1/2/1998   2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1  ...   
2       1/3/1998   2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2  ...   
3       1/4/1998   4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4  ...   
4       1/5/1998   2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3  ...   
...          ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
2531  12/27/2004   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3  ...   
2532  12/28/2004   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1  ...   
2533  12/29/2004   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5  ...   
2534  12/30/2004   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9  ...   
2535  12/31/2004   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6  ...   

      RH50    U50    V50    HT50     KI     TT      SLP  SLP_  Precp  Class  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0 -55.0   0.00      0  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0 -55.0   0.00      0  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0 -40.0   0.00      0  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0 -40.0   2.08      0  
4      NaN    NaN    NaN     NaN    NaN    NaN      NaN   NaN   0.58      0  
...    ...    ...    ...     ...    ...    ...      ...   ...    ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0  65.0   0.00      0  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0  15.0   0.00      0  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0 -35.0   0.00      0  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0 -30.0   0.05      0  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0 -25.0   0.00      0  

[2536 rows x 74 columns]

In [4]:
df.dtypes

date      object
WSR0     float64
WSR1     float64
WSR2     float64
WSR3     float64
          ...   
TT       float64
SLP      float64
SLP_     float64
Precp    float64
Class      int64
Length: 74, dtype: object

In [5]:
df.drop('date', axis=1, inplace=True)

In [6]:
df.isnull().sum()

WSR0     299
WSR1     292
WSR2     294
WSR3     292
WSR4     293
        ... 
TT       125
SLP       95
SLP_     159
Precp      2
Class      0
Length: 73, dtype: int64

In [7]:
null_counts = df.isnull().sum().sum()
total = df.size
null_percentages = 100 * null_counts / total
print("total nilai :",total)
print("nilai hilang :",null_counts)
print("persentase :",null_percentages)

total nilai : 185128
nilai hilang : 14938
persentase : 8.0690117108163


In [8]:
null_counts = df.isnull().sum()
null_percentages = 100 * null_counts / len(df)
null_percentages

WSR0     11.790221
WSR1     11.514196
WSR2     11.593060
WSR3     11.514196
WSR4     11.553628
           ...    
TT        4.929022
SLP       3.746057
SLP_      6.269716
Precp     0.078864
Class     0.000000
Length: 73, dtype: float64

# Imputasi

In [9]:
def jarak(df2,col):
    euc_dist[col] = []
    euc_dist_append =euc_dist[col].append
    for row in range(df2.shape[0]):
        current = df2.index[df2.iloc[:,col] == 0].tolist()
        current = current[0]
        a = df2.iloc[current,col+1:].tolist()
        b = df2.iloc[current,:col].tolist()
        x1 = b+a
        if(row is not current):
            a=df2.iloc[row,col+1:].tolist()
            b=df2.iloc[row,:col].tolist()
            x2=b+a
        else:
            continue
        dist = euclidean(x1,x2)
        euc_dist_append([dist,df2.iloc[row,col]])
#         print(" x1 = ",x1,"\n x2 = ",x2,"\n distance = ",euc_dist[col])

    lst = list(euc_dist[col])
    lst.sort()
    euc_dist[col] = lst
#     print(euc_dist[col])

In [10]:
from collections import Counter
def hitung(val, k, temp=None, i=0, counter=0):
    counts = Counter(val)
    total_count = len(counts)
#     print("jumlah val:", total_count)
    if counter >= int((k/2)+1) and total_count == 1 :
        print("median : ",int((k/2)+1))
        return temp
    elif i is not k:
        if temp is None:
            temp = val[i]
        elif temp != val[i]:
            temp = val[i]
            counter = 0
        # print(f"temp = {temp} , counter = {counter} , i = {i} , k = {k} , median = {int((k/2)+1)}, val[i] = {val[i]}")
        return hitung(val,k,temp,i+1,counter+1)
    else:
        return None
    
def Final(df,col,k):
    terdekat = []
    mean = 0
    std = 0
    diffsquared = 0
    sum_diffsquared = 0
    fuzzy_val = []
    euc_val = []
    terdekat_append = terdekat.append
    fuzzy_append = fuzzy_val.append
    
    for val in range(k):
        terdekat_append(euc_dist[col][val])
    
    for x,y in terdekat:
        mean += y  
        euc_val.append(y)
    mean /= len(terdekat)
    
    print(euc_val)
    
    for x,y in terdekat:
        diffsquared = (y-mean)**2
        sum_diffsquared = diffsquared + sum_diffsquared
    std_dev = ((sum_diffsquared)/len(terdekat))**(1/2)
    print("mean : ",mean)
    print("standar deviasi : ",std_dev)
    
    euc_val.sort()
    fuzzy = hitung(euc_val,3)
    
    for x,y in terdekat:
        if fuzzy is None:
            fuzzy_append((y,gaussian(y,mean,std_dev)))
        else:
            fuzzy_val.append((y,fuzzy))
        
    print("fuzzy : ",fuzzy_val)
    print("fuzzy : ",fuzzy)
    
    pembilang = 0
    penyebut = 0 
    
    for nilai,bobot in fuzzy_val:
        pembilang += nilai*bobot
        penyebut += bobot
            
    print("pembilang : ", pembilang)
    print("penyebut : ",penyebut)
    
    if fuzzy is not None:
        tertimbang = fuzzy
    else:
        tertimbang = pembilang / penyebut
    
    print("rata-rata tertimbang : ",tertimbang)
    index = dummy.index[dummy.iloc[:,col] == 0].tolist()
    index = index[0]
    
    if tertimbang == 0 and index == 0:
        tertimbang = dummy.iloc[index+1, col]
    elif tertimbang == 0:
        tertimbang = dummy.iloc[index-1, col]
        
    dummy.iloc[index,col] = tertimbang
    print(" ")

In [11]:
def gaussian(val, mean, std_dev):
    gaussian_mf = 2.718**((-1 * (val-mean)**2) / (2 * std_dev**2))
    return gaussian_mf

In [12]:
data = df.iloc[:, :-1]
df2 = data.copy()
dummy = df2.fillna(0)
dummy

WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  WSR9  ...   T50  \
0      0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9   2.3  ... -15.5   
1      2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1   3.4  ... -14.5   
2      2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2   2.5  ... -15.9   
3      4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4   3.1  ... -16.8   
4      2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3   1.4  ...   0.0   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
2531   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3   2.2  ... -12.4   
2532   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1   2.4  ... -12.0   
2533   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5   1.5  ... -11.8   
2534   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9   2.0  ... -10.8   
2535   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6   3.0  ... -11.9   

      RH50    U50    V50    HT50     KI     TT      SLP  SLP_  Precp  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0 -55.0   0.00  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0 -55.0   0.00  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0 -40.0   0.00  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0 -40.0   2.08  
4     0.00   0.00   0.00     0.0   0.00   0.00      0.0   0.0   0.58  
...    ...    ...    ...     ...    ...    ...      ...   ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0  65.0   0.00  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0  15.0   0.00  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0 -35.0   0.00  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0 -30.0   0.05  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0 -25.0   0.00  

[2536 rows x 72 columns]

In [13]:
count_zeros = np.count_nonzero(dummy == 0)

print("Jumlah angka 0 dalam dataset:", count_zeros)

Jumlah angka 0 dalam dataset: 17215


In [14]:
euc_dist = {}

In [15]:
for i in range(dummy.shape[1]):
    print("Kolom :",i+1)
    current = dummy.index[dummy.iloc[:,i] == 0].tolist()
    for x in current:
        jarak(dummy,i)
        Final(dummy,i,5)

Kolom : 1
[1.1, 0.4, 1.1, 0.4, 1.0]
mean :  0.8
standar deviasi :  0.3286335345030997
fuzzy :  [(1.1, 0.6592691111840654), (0.4, 0.47679724679977403), (1.1, 0.6592691111840654), (0.4, 0.47679724679977403), (1.0, 0.8309663449591802)]
fuzzy :  None
pembilang :  2.662796187003943
penyebut :  3.1030990609268594
rata-rata tertimbang :  0.8581086632176663
 
[0.0, 0.4, 4.6, 1.0, 3.8]
mean :  1.9600000000000002
standar deviasi :  1.8736061485808588
fuzzy :  [(0.0, 0.5786153380656931), (0.4, 0.707094311517527), (4.6, 0.37061019516033805), (1.0, 0.8769954438858311), (3.8, 0.6174394642558843)]
fuzzy :  None
pembilang :  5.210910030402757
penyebut :  3.1507547528852733
rata-rata tertimbang :  1.6538608806765795
 
[0.5, 0.4, 0.3, 1.0, 1.2]
mean :  0.68
standar deviasi :  0.354400902933387
fuzzy :  [(0.5, 0.8790025164636528), (0.4, 0.731930620120567), (0.3, 0.5628280232729844), (1.0, 0.6652442277985379), (1.2, 0.3408470241667522)]
fuzzy :  None
pembilang :  1.975382570060589
penyebut :  3.1798524118

[0.0, 0.2, 2.0, 0.0, 0.1]
mean :  0.4600000000000001
standar deviasi :  0.7735631842325487
fuzzy :  [(0.0, 0.8379586855603034), (0.2, 0.9450871809960791), (2.0, 0.13787439568566923), (0.0, 0.8379586855603034), (0.1, 0.897378501451191)]
fuzzy :  None
pembilang :  0.5545040777156734
penyebut :  3.656257449253546
rata-rata tertimbang :  0.15165892594048044
 
[0.0, 0.2, 0.6, 2.5, 2.8]
mean :  1.22
standar deviasi :  1.1872657663724664
fuzzy :  [(0.0, 0.5898444319020273), (0.2, 0.6914236134910748), (0.6, 0.8725488827756152), (2.5, 0.5592842049307799), (2.8, 0.41254597696891765)]
fuzzy :  None
pembilang :  3.215153300203503
penyebut :  3.1256471100684142
rata-rata tertimbang :  1.028636051026608
 
[0.0, 0.0, 0.8, 0.0, 0.4]
mean :  0.24000000000000005
standar deviasi :  0.32
fuzzy :  [(0.0, 0.7548616143394907), (0.0, 0.7548616143394907), (0.8, 0.2162995052279787), (0.0, 0.7548616143394907), (0.4, 0.8825083402897205)]
fuzzy :  None
pembilang :  0.5260429402982711
penyebut :  3.3633926885361713

[0.0, 1.2, 1.3, 1.4, 1.2]
mean :  1.02
standar deviasi :  0.515363949069005
fuzzy :  [(0.0, 0.14108661831032684), (1.2, 0.9408348573328537), (1.3, 0.8627976754649662), (1.4, 0.7619996640764252), (1.2, 0.9408348573328537)]
fuzzy :  None
pembilang :  4.4464401654103
penyebut :  3.6475536725174256
rata-rata tertimbang :  1.2190198046740484
 
[0.0, 2.4, 1.2, 0.7, 1.9]
mean :  1.2399999999999998
standar deviasi :  0.849941174435031
fuzzy :  [(0.0, 0.3450313490205286), (2.4, 0.39406342221687596), (1.2, 0.9988933079457749), (0.7, 0.8172532013080742), (1.9, 0.7397346365740364)]
fuzzy :  None
pembilang :  4.121997233261753
penyebut :  3.2949759170652904
rata-rata tertimbang :  1.2509946467023223
 
[0.0, 0.5728079132540242, 1.275256124356606, 0.25671826466600295, 0.746929961688786]
mean :  0.5703424527930838
standar deviasi :  0.43628961848452025
fuzzy :  [(0.0, 0.42555068314232525), (0.5728079132540242, 0.9999840350401121), (1.275256124356606, 0.2711427367815435), (0.25671826466600295, 0.772331

[0.0, 5.588108753735845e-06, 0.00015131596096959205, 0.0, 0.004097364788908945]
mean :  0.0008508537717264546
standar deviasi :  0.0016242884753693704
fuzzy :  [(0.0, 0.8718084099899304), (5.588108753735845e-06, 0.8733756338969437), (0.00015131596096959205, 0.9114394051396468), (0.0, 0.8718084099899304), (0.004097364788908945, 0.13570798067506246)]
fuzzy :  None
pembilang :  0.0006988409490712745
penyebut :  3.6641398396915137
rata-rata tertimbang :  0.00019072442091350706
 
[0.0, 0.0, 0.0, 5.588108753735845e-06, 0.0]
mean :  1.117621750747169e-06
standar deviasi :  2.235243501494338e-06
fuzzy :  [(0.0, 0.8825083402897205), (0.0, 0.8825083402897205), (0.0, 0.8825083402897205), (5.588108753735845e-06, 0.13536335042701722), (0.0, 0.8825083402897205)]
fuzzy :  None
pembilang :  7.564251234562277e-07
penyebut :  3.665396711585899
rata-rata tertimbang :  2.0636923721387497e-07
 
[0.0, 0.0, 0.004097364788908945, 0.00022648286762974042, 0.004097364788908945]
mean :  0.0016842424890895261
stan

[0.0, 0.00019872004384191246, 0.0, 2.0636923721387497e-07, 8.731317402168787e-06]
mean :  4.1531546096259026e-05
standar deviasi :  7.866586008001522e-05
fuzzy :  [(0.0, 0.8699230534853778), (0.00019872004384191246, 0.13585686903060123), (0.0, 0.8699230534853778), (2.0636923721387497e-07, 0.8711256112287477), (8.731317402168787e-06, 0.916752926590157)]
fuzzy :  None
pembilang :  3.518171727931858e-05
penyebut :  3.6635815138202616
rata-rata tertimbang :  9.603093897761334e-06
 
[0.0, 2.4, 0.0, 0.0, 0.0]
mean :  0.48
standar deviasi :  0.9600000000000001
fuzzy :  [(0.0, 0.8825083402897205), (2.4, 0.13536335042701728), (0.0, 0.8825083402897205), (0.0, 0.8825083402897205), (0.0, 0.8825083402897205)]
fuzzy :  None
pembilang :  0.32487204102484146
penyebut :  3.665396711585899
rata-rata tertimbang :  0.08863216360672725
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.

...

[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0,

[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0,

[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0,

[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0,

[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0,

In [16]:
dummy

WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  WSR9  ...   T50  \
0      0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9   2.3  ... -15.5   
1      2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1   3.4  ... -14.5   
2      2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2   2.5  ... -15.9   
3      4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4   3.1  ... -16.8   
4      2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3   1.4  ... -16.8   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
2531   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3   2.2  ... -12.4   
2532   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1   2.4  ... -12.0   
2533   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5   1.5  ... -11.8   
2534   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9   2.0  ... -10.8   
2535   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6   3.0  ... -11.9   

      RH50    U50    V50    HT50     KI     TT         SLP       SLP_  Precp  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0000 -55.000000   0.00  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0000 -55.000000   0.00  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0000 -40.000000   0.00  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0000 -40.000000   2.08  
4     0.49   8.73  10.54  5775.0  31.15  51.70  10195.8618 -12.375361   0.58  
...    ...    ...    ...     ...    ...    ...         ...        ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0000  65.000000   0.00  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0000  15.000000   0.00  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0000 -35.000000   0.00  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0000 -30.000000   0.05  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0000 -25.000000   0.00  

[2536 rows x 72 columns]

In [17]:
dummy.describe()

WSR0          WSR1          WSR2          WSR3          WSR4  \
count  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03   
mean   1.517344e+00  1.466480e+00  1.430790e+00  1.412681e+00  1.413174e+00   
std    1.266935e+00  1.261010e+00  1.231676e+00  1.199739e+00  1.191006e+00   
min    2.201199e-09  8.806461e-11  1.926049e-09  4.064521e-11  3.387100e-11   
25%    5.000000e-01  5.000000e-01  5.000000e-01  4.945784e-01  5.000000e-01   
50%    1.200000e+00  1.100000e+00  1.100000e+00  1.100000e+00  1.100000e+00   
75%    2.200000e+00  2.100000e+00  2.100000e+00  2.100000e+00  2.100000e+00   
max    7.500000e+00  7.700000e+00  7.100000e+00  7.300000e+00  7.200000e+00   

               WSR5          WSR6          WSR7          WSR8          WSR9  \
count  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03   
mean   1.432272e+00  1.517582e+00  1.890477e+00  2.343451e+00  2.642694e+00   
std    1.169831e+00  1.168679e+00  1.210459e+00  1.288729e+00  1.349110e+00   
min    3.387100e-11  4.403231e-11  2.384632e-09  1.016130e-10  3.485231e-09   
25%    5.045478e-01  6.000000e-01  1.000000e+00  1.400000e+00  1.700000e+00   
50%    1.200000e+00  1.300000e+00  1.700000e+00  2.300000e+00  2.600000e+00   
75%    2.000000e+00  2.100000e+00  2.600000e+00  3.200000e+00  3.500000e+00   
max    7.400000e+00  7.400000e+00  7.500000e+00  9.200000e+00  8.500000e+00   

       ...          T50         RH50          U50          V50         HT50  \
count  ...  2536.000000  2536.000000  2536.000000  2536.000000  2536.000000   
mean   ...   -10.126576     0.292658     9.640705     0.764709  5627.706166   
std    ...     4.272202     0.250413     9.478981     7.111992  1016.579782   
min    ...   -24.800000     0.000002   -14.920000   -25.990000     0.013772   
25%    ...   -13.200000     0.080000     2.040000    -3.462500  5760.000000   
50%    ...    -9.800000     0.210000     8.960000     0.090000  5830.000000   
75%    ...    -7.000000     0.460000    16.520271     4.560000  5880.000000   
max    ...    -0.000022     1.000000    42.360000    30.420000  5965.000000   

                KI           TT           SLP         SLP_        Precp  
count  2536.000000  2536.000000   2536.000000  2536.000000  2536.000000  
mean     10.123405    36.014292   9831.600058    -0.001265     0.371439  
std      20.337459    12.943051   1787.779631    35.047978     1.317001  
min     -56.700000   -10.100000      0.002796  -135.000000     0.000000  
25%      -2.700000    30.375000  10125.000000   -20.000000     0.000000  
50%      13.450000    40.650000  10155.000000    -1.480385     0.000000  
75%      27.800000    45.000000  10190.000000    15.000000     0.050000  
max      42.050000    59.150000  10350.000000   140.000000    20.650000  

[8 rows x 72 columns]

# Klasifikasi

In [57]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score

In [58]:
x = dummy.values
y = df.iloc[:, -1].values

In [59]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.25, random_state=3)

In [60]:
scaler = MinMaxScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.transform(x_test)

In [61]:
classifier = KNeighborsClassifier(n_neighbors=3, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[610   5]
 [ 17   2]]
0.9652996845425867


C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


In [62]:
classifier = KNeighborsClassifier(n_neighbors=5, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[614   1]
 [ 17   2]]
0.9716088328075709


C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


In [63]:
classifier = KNeighborsClassifier(n_neighbors=7, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[614   1]
 [ 19   0]]
0.9684542586750788


C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


In [64]:
classifier = KNeighborsClassifier(n_neighbors=9, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


[[614   1]
 [ 19   0]]
0.9684542586750788
